In [1]:
from pyomo.environ import *
from pyomo.opt import *
opt = solvers.SolverFactory("glpk")

In [2]:
F = ['Broccoli', 'Milk', 'Oranges']
N = ['Calcium', 'Vitamin C', 'Water']

c = {'Broccoli':38, 'Milk':10, 'Oranges':27}
r = {'Calcium':1000, 'Vitamin C':90, 'Water':3700}

a = {('Broccoli','Calcium'):47, 
     ('Broccoli','Vitamin C'):89, 
     ('Broccoli','Water'):91,
     ('Milk','Calcium'):276,    
     ('Milk','Vitamin C'):0,      
     ('Milk','Water'):87,
     ('Oranges','Calcium'):40,  
     ('Oranges','Vitamin C'):53,  
     ('Oranges','Water'):87}

model = ConcreteModel()
model.x = Var(F, within=NonNegativeReals)

In [3]:
def nutrition_rule (model, n):
    return sum(a[i,n]*model.x[i] for i in F) >= r[n]

model.c = Constraint(N, rule=nutrition_rule)

model.z = Objective(expr = sum(c[i]*model.x[i] for i in F), 
                    sense=minimize)

In [4]:
model.dual = Suffix(direction=Suffix.IMPORT)
results = opt.solve(model)

In [5]:
model.x.get_values()

{'Broccoli': 1.01123595505618, 'Milk': 41.4710060699987, 'Oranges': 0.0}

In [6]:
model.z.expr()

453.1370269921219

In [7]:
for n in N:
    print("Shadow price of", n, "is", model.dual[model.c[n]])

Shadow price of Calcium is 0.0
Shadow price of Vitamin C is 0.309440785225365
Shadow price of Water is 0.114942528735632
